In [1]:
from alpaca.trading.client import TradingClient
from alpaca.trading.requests import GetAssetsRequest
from alpaca.trading.enums import AssetClass
import pandas as pd
from alpaca_secrets import APCA_API_KEY_ID, APCA_API_SECRET_KEY


trading_client = TradingClient(APCA_API_KEY_ID, APCA_API_SECRET_KEY)
import pandas as pd
from backtesting import Strategy
from backtesting import Backtest, Strategy
from backtesting.lib import crossover
from ta.trend import ADXIndicator
import numpy as np


from alpaca.data.historical import StockHistoricalDataClient
from alpaca.data.requests import StockBarsRequest
from alpaca.data.timeframe import TimeFrame
import datetime

# search for US equities
search_params = GetAssetsRequest(asset_class=AssetClass.US_EQUITY)

assets = trading_client.get_all_assets(search_params)

/Users/guilistocco/Trabalho_Final/trading_strategy/trading_env/lib/python3.10/site-packages/backtesting/_plotting.py:55: UserWarning: Jupyter Notebook detected. Setting Bokeh output to notebook. This may not work in Jupyter clients without JavaScript support, such as old IDEs. Reset with `backtesting.set_bokeh_output(notebook=False)`.
  warnings.warn('Jupyter Notebook detected. '


Loading BokehJS ...

In [2]:
import random

asasd = random.sample(assets, 5)  # Display 5 random assets
# Exibe apenas os símbolos dos 5 ativos sorteados
for asss in asasd:
    print(asss.symbol)
    try:
        asset = trading_client.get_asset(asss.symbol)
        print(f"{asset.symbol}: Tradable = {asset.tradable}")
    except Exception as e:
        print(f"{asset.symbol}: Error - {e}")

EOLS
EOLS: Tradable = True
DAKT
DAKT: Tradable = True
DRLL
DRLL: Tradable = True
VERKF
VERKF: Tradable = False
ROYHF
ROYHF: Tradable = False


In [3]:
symbols_list = [
    "GOAU",
    "PTMN",
    "NKTX",
    "GLP",
    "QQQ",
    "AAPL",
]

In [4]:
from alpaca.trading.requests import GetAssetsRequest

symbols = symbols_list

for symbol in symbols:
    try:
        asset = trading_client.get_asset(symbol)
        print(f"{symbol}: Tradable = {asset.tradable}")
    except Exception as e:
        print(f"{symbol}: Error - {e}")


GOAU: Tradable = True
PTMN: Tradable = True
NKTX: Tradable = True
GLP: Tradable = True
QQQ: Tradable = True
AAPL: Tradable = True


In [36]:
from alpaca.data.historical import StockHistoricalDataClient
from alpaca.data.requests import StockBarsRequest
from alpaca.data.timeframe import TimeFrame
import datetime

# Crie o client de dados históricos (usa as mesmas credenciais)
data_client = StockHistoricalDataClient(APCA_API_KEY_ID, APCA_API_SECRET_KEY)

# Defina o período de 3 anos

end_date = datetime.datetime.now()
start_date = end_date - datetime.timedelta(days=5*365)

# Solicite os dados OHLC para os símbolos desejados
bars_request = StockBarsRequest(
    symbol_or_symbols=symbols,
    timeframe=TimeFrame.Hour,
    start=start_date,
    end=end_date
)

bars = data_client.get_stock_bars(bars_request).data

dfs = {}
for sym in symbols:
    candle = bars.get(sym, None)
    if candle is not None:
        dfs[sym] = pd.DataFrame([{k: getattr(bar, k) for k in ['timestamp', 'open', 'high', 'low', 'close', 'volume', 'vwap']} for bar in candle])
    
    
        # Supondo que df tenha ['open', 'high', 'low', 'close', 'volume']
        df = dfs[sym][['timestamp', 'open', 'high', 'low', 'close', 'volume']].copy()
        df.columns = ['Timestamp', 'Open', 'High', 'Low', 'Close', 'Volume']
        df['Timestamp'] = pd.to_datetime(df['Timestamp'])
        df.set_index('Timestamp', inplace=True)
        dfs[sym] = df  # Atualiza o dict para manter o formato padronizado


In [37]:
dfs.keys()

dict_keys(['GOAU', 'PTMN', 'NKTX', 'GLP', 'QQQ', 'AAPL'])

# Candles Stocks

In [113]:
# import mplfinance as mpf

# dfs = [df_goau, df_ring, df_iau, df_spy, df_qqq]
# symbols = ["GOAU", "RING", "IAU", "SPY", "QQQ"]

# for df, symbol in zip(dfs, symbols):
#     df_plot = df.copy()
#     df_plot.set_index('timestamp', inplace=True)
#     mpf.plot(df_plot, type='candle', title=symbol, style='yahoo', volume=True)

# Estrategias

In [119]:
dfs["TOPP"]

Open    High     Low   Close    Volume
Timestamp                                                          
2025-01-22 16:00:00+00:00  3.8800  3.9000  3.7500  3.7700  294595.0
2025-01-22 17:00:00+00:00  3.7700  3.7900  3.7500  3.7700   59027.0
2025-01-22 18:00:00+00:00  3.7800  3.7900  3.7500  3.7700   12772.0
2025-01-22 19:00:00+00:00  3.7550  3.7700  3.7500  3.7500    2803.0
2025-01-22 20:00:00+00:00  3.7500  3.8400  3.7500  3.7947   18328.0
...                           ...     ...     ...     ...       ...
2025-07-11 15:00:00+00:00  1.7100  1.7100  1.7100  1.7100     100.0
2025-07-11 16:00:00+00:00  1.6900  1.7200  1.6900  1.7200     200.0
2025-07-11 18:00:00+00:00  1.6900  1.6900  1.6900  1.6900     100.0
2025-07-11 19:00:00+00:00  1.7404  1.7404  1.7404  1.7404     100.0
2025-07-11 20:00:00+00:00  1.7500  1.7700  1.7500  1.7700     203.0

[925 rows x 5 columns]

In [127]:
import pandas as pd
from backtesting import Strategy
from backtesting.lib import crossover

def rolling_mean(data, window):
    series = pd.Series(data)
    return series.rolling(window=window, min_periods=window).mean().to_numpy()


class TripleMovingAverage(Strategy):
    fast = 9
    mid = 35
    slow = 70

    def init(self):
        self.ma_fast = self.I(rolling_mean, self.data.Close, self.fast)
        self.ma_mid = self.I(rolling_mean, self.data.Close, self.mid)
        self.ma_slow = self.I(rolling_mean, self.data.Close, self.slow)

    def next(self):
        buffer = 0.01  # ajuste conforme o ativo e timeframe

        if len(self.data) < self.slow:
            return

        # Compra: fast > mid > slow com buffer e cruzamento recente
        if (
            self.ma_fast[-1] > self.ma_mid[-1] + buffer and
            self.ma_mid[-1] > self.ma_slow[-1] + buffer and
            (
                self.ma_fast[-2] <= self.ma_mid[-2] or
                self.ma_mid[-2] <= self.ma_slow[-2]
            )
        ):
            self.buy(size=10)

        # Venda: fast < mid < slow com buffer e cruzamento recente
        elif (
            self.ma_fast[-1] < self.ma_mid[-1] - buffer and
            self.ma_mid[-1] < self.ma_slow[-1] - buffer and
            (
                self.ma_fast[-2] >= self.ma_mid[-2] or
                self.ma_mid[-2] >= self.ma_slow[-2]
            )
        ):
            self.sell(size=10)
            # Se não está mais alinhado, zera a posição
        elif not (
            (self.ma_fast[-1] > self.ma_mid[-1] + buffer and self.ma_mid[-1] > self.ma_slow[-1] + buffer) or
            (self.ma_fast[-1] < self.ma_mid[-1] - buffer and self.ma_mid[-1] < self.ma_slow[-1] - buffer)
        ):
            self.position.close()

In [138]:
# Supondo que df tenha ['open', 'high', 'low', 'close', 'volume']
df_bt = dfs["TOPP"].reset_index()[['timestamp', 'open', 'high', 'low', 'close', 'volume']].copy()
df_bt.columns = ['Timestamp', 'Open', 'High', 'Low', 'Close', 'Volume']
df_bt['Timestamp'] = pd.to_datetime(df_bt['Timestamp'])
df_bt.set_index('Timestamp', inplace=True)



# df_bt precisa ter as colunas: Open, High, Low, Close, Volume (com esses nomes

bt = Backtest(df_bt, TripleMovingAverage, cash=100_000, commission=.01, exclusive_orders=False)
results = bt.run()
bt.plot()

/Users/guilistocco/Trabalho_Final/trading_strategy/trading_env/lib/python3.10/site-packages/bokeh/util/serialization.py:242: UserWarning: no explicit representation of timezones available for np.datetime64
  return convert(array.astype("datetime64[us]"))


GridPlot(id='p6940', ...)

In [139]:

bt = Backtest(
    df_bt,
    TripleMovingAverage,
    cash=100_000,
    commission=0.001,
    exclusive_orders=True
)

if __name__ == "__main__":
    stats = bt.optimize(
        fast=range(5, 20, 2),
        mid=range(10, 40, 5),
        slow=range(30, 100, 10),
        maximize="Sharpe Ratio",
        constraint=lambda p: p.fast < p.mid < p.slow
    )

    print(stats)
    bt.plot()

/Users/guilistocco/Trabalho_Final/trading_strategy/trading_env/lib/python3.10/site-packages/backtesting/backtesting.py:1606: RuntimeWarning: If you want to use multi-process optimization with `multiprocessing.get_start_method() == 'spawn'` (e.g. on Windows),set `backtesting.Pool = multiprocessing.Pool` (or of the desired context) and hide `bt.optimize()` call behind a `if __name__ == '__main__'` guard. Currently using thread-based paralellism, which might be slightly slower for non-numpy / non-GIL-releasing code. See https://github.com/kernc/backtesting.py/issues/1256
  output = _optimize_grid()
Traceback (most recent call last):
  File "/opt/homebrew/Cellar/python@3.10/3.10.8/Frameworks/Python.framework/Versions/3.10/lib/python3.10/multiprocessing/resource_tracker.py", line 209, in main
    cache[rtype].remove(name)
KeyError: '/psm_35bbcad8'
Traceback (most recent call last):
  File "/opt/homebrew/Cellar/python@3.10/3.10.8/Frameworks/Python.framework/Versions/3.10/lib/python3.10/multi

Start                     2025-01-22 16:00...
End                       2025-07-11 20:00...
Duration                    170 days 04:00:00
Exposure Time [%]                    13.72973
Equity Final [$]                 100012.81509
Equity Peak [$]                  100013.38164
Commissions [$]                       0.83591
Return [%]                            0.01282
Buy & Hold Return [%]                -4.32432
Return (Ann.) [%]                     0.02691
Volatility (Ann.) [%]                 0.00718
CAGR [%]                              0.01898
Sharpe Ratio                          3.74637
Sortino Ratio                         8.73755
Calmar Ratio                          8.55374
Alpha [%]                              0.0128
Beta                                     -0.0
Max. Drawdown [%]                    -0.00315
Avg. Drawdown [%]                    -0.00107
Max. Drawdown Duration       20 days 03:00:00
Avg. Drawdown Duration        5 days 23:00:00
# Trades                          

In [140]:
print(f"fast={stats._strategy.fast}, mid={stats._strategy.mid}, slow={stats._strategy.slow}")

fast=7, mid=10, slow=80


In [141]:
stats

Start                     2025-01-22 16:00...
End                       2025-07-11 20:00...
Duration                    170 days 04:00:00
Exposure Time [%]                    13.72973
Equity Final [$]                 100012.81509
Equity Peak [$]                  100013.38164
Commissions [$]                       0.83591
Return [%]                            0.01282
Buy & Hold Return [%]                -4.32432
Return (Ann.) [%]                     0.02691
Volatility (Ann.) [%]                 0.00718
CAGR [%]                              0.01898
Sharpe Ratio                          3.74637
Sortino Ratio                         8.73755
Calmar Ratio                          8.55374
Alpha [%]                              0.0128
Beta                                     -0.0
Max. Drawdown [%]                    -0.00315
Avg. Drawdown [%]                    -0.00107
Max. Drawdown Duration       20 days 03:00:00
Avg. Drawdown Duration        5 days 23:00:00
# Trades                          

In [142]:
stats[['Return [%]', 'Sharpe Ratio', 'Max. Drawdown [%]', 'Win Rate [%]']]

Return [%]           0.012815
Sharpe Ratio         3.746369
Max. Drawdown [%]   -0.003146
Win Rate [%]             84.0
dtype: object

In [143]:
stats['_trades'].head()

Size  EntryBar  ExitBar  EntryPrice  ExitPrice    SL    TP   PnL  \
0    10       130      143        2.07      2.250  None  None  1.80   
1    10       148      155        2.40      2.250  None  None -1.50   
2    10       160      163        2.25      2.330  None  None  0.80   
3    10       211      212        2.29      2.381  None  None  0.91   
4   -10       233      238        2.30      2.140  None  None  1.60   

   ReturnPct                 EntryTime                  ExitTime  \
0   0.086957 2025-02-06 22:00:00+00:00 2025-02-10 12:00:00+00:00   
1  -0.062500 2025-02-10 17:00:00+00:00 2025-02-11 15:00:00+00:00   
2   0.035556 2025-02-12 14:00:00+00:00 2025-02-12 17:00:00+00:00   
3   0.039738 2025-02-21 21:00:00+00:00 2025-02-24 14:00:00+00:00   
4   0.069565 2025-02-27 15:00:00+00:00 2025-02-28 14:00:00+00:00   

         Duration   Tag  Entry_rolling_m…(C,7)  Exit_rolling_m…(C,7)  \
0 3 days 14:00:00  None               2.053657              2.195029   
1 0 days 22:00:00  None               2.244557              2.333671   
2 0 days 03:00:00  None               2.333900              2.346457   
3 2 days 17:00:00  None               2.423414              2.392014   
4 0 days 23:00:00  None               2.281486              2.226571   

   Entry_rolling_m…(C,10)  Exit_rolling_m…(C,10)  Entry_rolling_m…(C,80)  \
0                 1.96272                2.22752                1.890818   
1                 2.22949                2.34341                1.917534   
2                 2.31773                2.35529                1.986786   
3                 2.42671                2.40939                2.373209   
4                 2.32542                2.22560                2.410304   

   Exit_rolling_m…(C,80)  
0               1.900510  
1               1.957416  
2               2.010231  
3               2.376334  
4               2.401655

In [144]:
(13.2600 - 13.6000) * 10

-3.3999999999999986

In [145]:
# Supondo que df tenha ['open', 'high', 'low', 'close', 'volume']
df_bt = df_goau[['timestamp', 'open', 'high', 'low', 'close', 'volume']].copy()
df_bt.columns = ['Timestamp', 'Open', 'High', 'Low', 'Close', 'Volume']
df_bt['Timestamp'] = pd.to_datetime(df_bt['Timestamp'])
df_bt.set_index('Timestamp', inplace=True)


NameError: name 'df_goau' is not defined

In [ ]:
df_bt

Open     High      Low    Close  Volume
Timestamp                                                            
2022-07-11 12:00:00+00:00  14.0000  14.0000  14.0000  14.0000   250.0
2022-07-11 13:00:00+00:00  13.8900  14.0550  13.8400  14.0550  5865.0
2022-07-11 14:00:00+00:00  14.0000  14.0688  13.9200  14.0350  7995.0
2022-07-11 15:00:00+00:00  14.0269  14.0269  13.9600  13.9600  1366.0
2022-07-11 16:00:00+00:00  13.9689  13.9689  13.9500  13.9500   725.0
...                            ...      ...      ...      ...     ...
2025-07-09 15:00:00+00:00  28.8500  28.8500  28.8500  28.8500   441.0
2025-07-09 16:00:00+00:00  28.8000  28.8850  28.7725  28.7725   858.0
2025-07-09 17:00:00+00:00  28.7600  29.0493  28.7600  29.0493  2145.0
2025-07-09 18:00:00+00:00  29.0400  29.0400  29.0400  29.0400   440.0
2025-07-09 19:00:00+00:00  28.9501  29.1100  28.9501  29.1100  2549.0

[5322 rows x 5 columns]

# estrat 1


In [38]:
dfs.keys()

dict_keys(['GOAU', 'PTMN', 'NKTX', 'GLP', 'QQQ', 'AAPL'])

In [39]:
dfs["PTMN"].reset_index()

Timestamp     Open     High      Low    Close    Volume
0     2020-07-13 20:00:00+00:00   1.1200   1.1200   1.1200   1.1200    1270.0
1     2020-07-14 13:00:00+00:00   1.1200   1.1200   1.0800   1.1100  144488.0
2     2020-07-14 14:00:00+00:00   1.1046   1.1100   1.1046   1.1100   13000.0
3     2020-07-14 15:00:00+00:00   1.1100   1.1200   1.1000   1.1000   32100.0
4     2020-07-14 16:00:00+00:00   1.1100   1.1155   1.1000   1.1100    5077.0
...                         ...      ...      ...      ...      ...       ...
10168 2025-07-11 16:00:00+00:00  12.5000  12.5100  12.4700  12.4700    3155.0
10169 2025-07-11 17:00:00+00:00  12.5400  12.5500  12.4800  12.5327    5078.0
10170 2025-07-11 18:00:00+00:00  12.5500  12.6600  12.5250  12.5600    6658.0
10171 2025-07-11 19:00:00+00:00  12.6000  12.7500  12.5200  12.7500   19382.0
10172 2025-07-11 20:00:00+00:00  12.7500  12.7500  12.7500  12.7500    4362.0

[10173 rows x 6 columns]

In [40]:
df_bt = dfs["PTMN"].reset_index()

In [11]:
class MACrossover(Strategy):
    short_window = 20
    long_window = 50
    buffer_pct = 0.001  # 0.1%

    def init(self):
        close = self.data.Close
        self.ma_short = self.I(lambda x: pd.Series(x).rolling(self.short_window).mean(), close, name='ma_short')
        self.ma_long = self.I(lambda x: pd.Series(x).rolling(self.long_window).mean(), close, name='ma_long')

    def next(self):
        if len(self.ma_short) < 2 or len(self.ma_long) < 2:
            return

        price = self.data.Close[-1]
        diff = self.ma_short[-1] - self.ma_long[-1]

        # Aplica o buffer
        if diff > self.buffer_pct * price and self.ma_short[-2] <= self.ma_long[-2]:
            if self.position.is_short:
                self.position.close()
            if not self.position.is_long:
                self.buy(size=10)

        elif diff < -self.buffer_pct * price and self.ma_short[-2] >= self.ma_long[-2]:
            if self.position.is_long:
                self.position.close()
            if not self.position.is_short:
                self.sell(size=10)

In [12]:
bt = Backtest(df_bt, MACrossover, cash=100_000, commission=.01, exclusive_orders=True)
results = bt.run()
bt.plot()

/var/folders/21/6bbwtzhx0js126xjwqnzpzzc0000gn/T/ipykernel_79000/2085031806.py:1: UserWarning: Data index is not datetime. Assuming simple periods, but `pd.DateTimeIndex` is advised.
  bt = Backtest(df_bt, MACrossover, cash=100_000, commission=.01, exclusive_orders=True)


GridPlot(id='p1699', ...)

In [13]:
results

Start                                     0.0
End                                    5825.0
Duration                               5825.0
Exposure Time [%]                    87.62444
Equity Final [$]                  99913.31744
Equity Peak [$]                      100000.0
Commissions [$]                      26.54456
Return [%]                           -0.08668
Buy & Hold Return [%]               -47.44435
Return (Ann.) [%]                         0.0
Volatility (Ann.) [%]                     NaN
Sharpe Ratio                              NaN
Sortino Ratio                             NaN
Calmar Ratio                              0.0
Alpha [%]                            -0.09685
Beta                                 -0.00021
Max. Drawdown [%]                    -0.09584
Avg. Drawdown [%]                    -0.09584
Max. Drawdown Duration                 5398.0
Avg. Drawdown Duration                 5398.0
# Trades                                  7.0
Win Rate [%]                      

# estrat 2

In [15]:
class DonchianBreakout(Strategy):
    window = 20
    buffer_pct = 0.002  # 0.2%

    def init(self):
        high = self.data.High
        low = self.data.Low
        self.highs = self.I(lambda x: pd.Series(x).rolling(self.window).max(), high, name='donchian_high')
        self.lows = self.I(lambda x: pd.Series(x).rolling(self.window).min(), low, name='donchian_low')

    def next(self):
        if len(self.highs) < 2 or len(self.lows) < 2:
            return

        close = self.data.Close[-1]
        high_break = self.highs[-2] * (1 + self.buffer_pct)
        low_break = self.lows[-2] * (1 - self.buffer_pct)

        if close > high_break:
            if self.position.is_short:
                self.position.close()
            if not self.position.is_long:
                self.buy(size=10)
        elif close < low_break:
            if self.position.is_long:
                self.position.close()
            if not self.position.is_short:
                self.sell(size=10)

In [16]:
bt = Backtest(df_bt, DonchianBreakout, cash=100_000, commission=.01, exclusive_orders=True)
results = bt.run()
bt.plot()

/var/folders/21/6bbwtzhx0js126xjwqnzpzzc0000gn/T/ipykernel_75242/399737157.py:1: UserWarning: Data index is not datetime. Assuming simple periods, but `pd.DateTimeIndex` is advised.
  bt = Backtest(df_bt, DonchianBreakout, cash=100_000, commission=.01, exclusive_orders=True)


GridPlot(id='p1670', ...)

# estrat 3

In [17]:
class ADXTrend(Strategy):
    window = 14
    min_adx = 30  # exige tendência mais forte

    def init(self):
        h, l, c = self.data.High, self.data.Low, self.data.Close
        adx_obj = ADXIndicator(pd.Series(h), pd.Series(l), pd.Series(c), self.window)

        self.adx = self.I(lambda: adx_obj.adx(), name='adx')
        self.di_plus = self.I(lambda: adx_obj.adx_pos(), name='di_plus')
        self.di_minus = self.I(lambda: adx_obj.adx_neg(), name='di_minus')

    def next(self):
        if len(self.adx) < 1:
            return

        if self.adx[-1] > self.min_adx:
            if self.di_plus[-1] > self.di_minus[-1]:
                if self.position.is_short:
                    self.position.close()
                if not self.position.is_long:
                    self.buy(size=10)
            elif self.di_minus[-1] > self.di_plus[-1]:
                if self.position.is_long:
                    self.position.close()
                if not self.position.is_short:
                    self.sell(size=10)
        else:
            self.position.close()

In [18]:
bt = Backtest(df_bt, ADXTrend, cash=100_000, commission=.01, exclusive_orders=True)
results = bt.run()
bt.plot()

/var/folders/21/6bbwtzhx0js126xjwqnzpzzc0000gn/T/ipykernel_75242/327853158.py:1: UserWarning: Data index is not datetime. Assuming simple periods, but `pd.DateTimeIndex` is advised.
  bt = Backtest(df_bt, ADXTrend, cash=100_000, commission=.01, exclusive_orders=True)


GridPlot(id='p2103', ...)

# estrat 4

In [19]:
from ta.momentum import RSIIndicator

class EMA_RSI_Filter(Strategy):
    short = 20
    long = 50
    rsi_period = 14
    ema_gap_pct = 0.001  # diferença mínima de 0.1%
    rsi_gap = 5  # RSI deve estar acima de 55 ou abaixo de 45

    def init(self):
        close = self.data.Close
        self.ema_short = self.I(lambda x: pd.Series(x).ewm(span=self.short).mean(), close, name='ema_short')
        self.ema_long = self.I(lambda x: pd.Series(x).ewm(span=self.long).mean(), close, name='ema_long')

        rsi_obj = RSIIndicator(pd.Series(close), self.rsi_period)
        self.rsi = self.I(lambda: rsi_obj.rsi(), name='rsi')

    def next(self):
        if any(len(arr) < 2 for arr in [self.ema_short, self.ema_long, self.rsi]):
            return

        price = self.data.Close[-1]
        ema_diff = self.ema_short[-1] - self.ema_long[-1]
        rsi_val = self.rsi[-1]

        if ema_diff > self.ema_gap_pct * price and rsi_val > 50 + self.rsi_gap:
            if self.position.is_short:
                self.position.close()
            if not self.position.is_long:
                self.buy(size=10)

        elif ema_diff < -self.ema_gap_pct * price and rsi_val < 50 - self.rsi_gap:
            if self.position.is_long:
                self.position.close()
            if not self.position.is_short:
                self.sell(size=10)
        else:
            self.position.close()

In [20]:
bt = Backtest(df_bt, EMA_RSI_Filter, cash=100_000, commission=.01, exclusive_orders=True)
results = bt.run()
bt.plot()

/var/folders/21/6bbwtzhx0js126xjwqnzpzzc0000gn/T/ipykernel_75242/849591965.py:1: UserWarning: Data index is not datetime. Assuming simple periods, but `pd.DateTimeIndex` is advised.
  bt = Backtest(df_bt, EMA_RSI_Filter, cash=100_000, commission=.01, exclusive_orders=True)


GridPlot(id='p2499', ...)

# estrat 5

In [21]:
from sklearn.linear_model import LinearRegression

class LinearSlope(Strategy):
    window = 10
    slope_threshold = 0.01  # mínimo para entrar (ajustável)


    def init(self):
        pass

    def slope(self, series):
        X = np.arange(len(series)).reshape(-1, 1)
        y = np.array(series).reshape(-1, 1)
        reg = LinearRegression().fit(X, y)
        return reg.coef_[0][0]

    def next(self):
        if len(self.data.Close) < self.window:
            return

        slp = self.slope(self.data.Close[-self.window:])

        if slp > self.slope_threshold:
            if self.position.is_short:
                self.position.close()
            if not self.position.is_long:
                self.buy(size=10)
        elif slp < -self.slope_threshold:
            if self.position.is_long:
                self.position.close()
            if not self.position.is_short:
                self.sell(size=10)
        else:
            self.position.close()

In [22]:
bt = Backtest(df_bt, LinearSlope, cash=100_000, commission=.01, exclusive_orders=True)
results = bt.run()
bt.plot()

/var/folders/21/6bbwtzhx0js126xjwqnzpzzc0000gn/T/ipykernel_75242/2217140206.py:1: UserWarning: Data index is not datetime. Assuming simple periods, but `pd.DateTimeIndex` is advised.
  bt = Backtest(df_bt, LinearSlope, cash=100_000, commission=.01, exclusive_orders=True)


GridPlot(id='p2825', ...)

In [19]:
dfs.keys()

NameError: name 'dfs' is not defined

# recomeco

In [41]:
dfs.keys()

dict_keys(['GOAU', 'PTMN', 'NKTX', 'GLP', 'QQQ', 'AAPL'])

In [ ]:
import datetime
# import pandas_ta as ta
import pandas as pd
from  import Backtest
from backtesting import Strategy
from backtesting.lib import crossover
import talib

class RsiOscillator(Strategy):
    upper_bound = 80
    lower_bound = 20
    rsi_window = 14

    # Do as much initial computation as possible
    def init(self):
        self.rsi = self.I(talib.RSI, pd.Series(self.data.Close), self.rsi_window)


    def next(self):
        # if crossover(self.rsi, self.upper_bound):
        #     self.sell(size=100)
        # if self.position.is_short and crossover(self.upper_bound, self.rsi):
        #     self.position.close()

        if crossover(self.lower_bound, self.rsi):
            self.buy(size=100)
        if self.position.is_long and crossover(self.rsi, self.lower_bound):
            self.position.close()

ticker = "GOAU"
df_int = dfs[ticker].reset_index()
df_int["Timestamp"] = pd.to_datetime(df_int["Timestamp"])
df_int['Timestamp'] = df_int['Timestamp'].dt.tz_localize(None)
df_int.set_index('Timestamp', inplace=True)

bt = Backtest(df_int, RsiOscillator, cash=10_000, commission=.002)
stats, heatmap_ = bt.optimize(
    upper_bound = range(55, 85, 5),
    lower_bound = range(10, 45, 5),
    rsi_window = 14,
    # rsi_window = range(10, 30, 2),
    maximize = "Return [%]",
    # maximize = "Return [%]",
    constraint = lambda param: param.upper_bound > param.lower_bound,
    # max_tries = 100,
    return_heatmap=True,
)
bt.plot()

/Users/guilistocco/Trabalho_Final/trading_strategy/trading_env/lib/python3.10/site-packages/backtesting/backtesting.py:1606: RuntimeWarning: If you want to use multi-process optimization with `multiprocessing.get_start_method() == 'spawn'` (e.g. on Windows),set `backtesting.Pool = multiprocessing.Pool` (or of the desired context) and hide `bt.optimize()` call behind a `if __name__ == '__main__'` guard. Currently using thread-based paralellism, which might be slightly slower for non-numpy / non-GIL-releasing code. See https://github.com/kernc/backtesting.py/issues/1256
  output = _optimize_grid()
Traceback (most recent call last):
  File "/opt/homebrew/Cellar/python@3.10/3.10.8/Frameworks/Python.framework/Versions/3.10/lib/python3.10/multiprocessing/resource_tracker.py", line 209, in main
    cache[rtype].remove(name)
KeyError: '/psm_9f514cef'
Traceback (most recent call last):
  File "/opt/homebrew/Cellar/python@3.10/3.10.8/Frameworks/Python.framework/Versions/3.10/lib/python3.10/multi

GridPlot(id='p6344', ...)

In [60]:
print(f"upper_bound={stats._strategy.upper_bound}, lower_bound={stats._strategy.lower_bound}, rsi_window={stats._strategy.rsi_window}")

upper_bound=55, lower_bound=20, rsi_window=14


In [61]:
stats

Start                     2020-07-13 21:00:00
End                       2025-07-11 19:00:00
Duration                   1823 days 22:00:00
Exposure Time [%]                     0.76889
Equity Final [$]                  10060.76986
Equity Peak [$]                   10060.76986
Commissions [$]                     146.90014
Return [%]                             0.6077
Buy & Hold Return [%]                33.77115
Return (Ann.) [%]                     0.12153
Volatility (Ann.) [%]                 0.52681
CAGR [%]                              0.08374
Sharpe Ratio                           0.2307
Sortino Ratio                         0.42827
Calmar Ratio                          0.10093
Alpha [%]                             0.56969
Beta                                  0.00113
Max. Drawdown [%]                    -1.20421
Avg. Drawdown [%]                    -1.20421
Max. Drawdown Duration     1656 days 21:00:00
Avg. Drawdown Duration     1656 days 21:00:00
# Trades                          

In [62]:
import seaborn as sns
import matplotlib.pyplot as plt

In [63]:
heatmap_

upper_bound  lower_bound  rsi_window
55           10           14                  NaN
             15           14             0.270126
             20           14             0.607699
             25           14            -1.745648
             30           14           -10.439658
             35           14           -16.805745
             40           14           -21.969308
60           10           14                  NaN
             15           14             0.270126
             20           14             0.607699
             25           14            -1.745648
             30           14           -10.439658
             35           14           -16.805745
             40           14           -21.969308
65           10           14                  NaN
             15           14             0.270126
             20           14             0.607699
             25           14            -1.745648
             30           14           -10.439658
             

In [64]:
hm = heatmap_.groupby(["upper_bound","lower_bound"]).mean().unstack()
sns.heatmap(hm, cmap="plasma")
plt.show()

In [22]:
dfs.keys()

dict_keys(['GOAU', 'PTMN', 'NKTX', 'GLP', 'QQQ', 'AAPL'])

In [67]:
df_int

Timestamp     Open     High      Low    Close   Volume
0    2022-07-13 19:00:00+00:00  13.9800  13.9800  13.9005  13.9500   1863.0
1    2022-07-14 13:00:00+00:00  13.4800  13.5100  13.0555  13.1733  12147.0
2    2022-07-14 14:00:00+00:00  13.1700  13.3000  13.1100  13.3000   6646.0
3    2022-07-14 15:00:00+00:00  13.2900  13.4300  13.2810  13.4300   1655.0
4    2022-07-14 16:00:00+00:00  13.2801  13.3199  13.2500  13.2500   1754.0
...                        ...      ...      ...      ...      ...      ...
5308 2025-07-11 15:00:00+00:00  29.6300  29.8000  29.6300  29.6995   1877.0
5309 2025-07-11 16:00:00+00:00  29.7998  29.7998  29.5950  29.6100   3324.0
5310 2025-07-11 17:00:00+00:00  29.7000  29.7000  29.6300  29.6940   2711.0
5311 2025-07-11 18:00:00+00:00  29.6992  29.7800  29.5900  29.6950   1489.0
5312 2025-07-11 19:00:00+00:00  29.6992  29.7900  29.5901  29.7800   1705.0

[5313 rows x 6 columns]

In [65]:
from backtesting import Backtest, Strategy
from backtesting.lib import crossover
from backtesting.test import GOOG  # Dados de exemplo
import pandas as pd
import numpy as np
import talib

class MeanReversionBB(Strategy):
    def init(self):
        # Calcula as bandas de Bollinger
        close = self.data.Close
        self.bb_upper, self.bb_middle, self.bb_lower = self.I(
            talib.BBANDS, close, timeperiod=20, nbdevup=2, nbdevdn=2, matype=0
        )

    def next(self):
        price = self.data.Close[-1]
        if not self.position:
            # Compra se o preço fecha abaixo da banda inferior
            if price < self.bb_lower[-1]:
                self.buy(size=10)
            # Venda descoberta se o preço fecha acima da banda superior
            elif price > self.bb_upper[-1]:
                self.sell(size=10)
        else:
            # Fecha posição se o preço voltar à média
            if self.position.is_long and price >= self.bb_middle[-1]:
                self.position.close()
            elif self.position.is_short and price <= self.bb_middle[-1]:
                self.position.close()

# Rodando o backtest
bt = Backtest(GOOG, MeanReversionBB, cash=10_000, commission=0.002)
result = bt.run()
bt.plot()
print(result)

Start                     2004-08-19 00:00:00
End                       2013-03-01 00:00:00
Duration                   3116 days 00:00:00
Exposure Time [%]                    42.87709
Equity Final [$]                    4750.5164
Equity Peak [$]                       10000.0
Commissions [$]                      767.2836
Return [%]                          -52.49484
Buy & Hold Return [%]               607.37036
Return (Ann.) [%]                    -8.36197
Volatility (Ann.) [%]                14.50612
CAGR [%]                             -5.84203
Sharpe Ratio                         -0.57644
Sortino Ratio                        -0.73604
Calmar Ratio                         -0.15088
Alpha [%]                          -105.34867
Beta                                  0.08702
Max. Drawdown [%]                   -55.42155
Avg. Drawdown [%]                   -55.42155
Max. Drawdown Duration     3087 days 00:00:00
Avg. Drawdown Duration     3087 days 00:00:00
# Trades                          